In [0]:
import pyspark.sql.functions as F
import pandas as pd
from functools import reduce
from pyspark.sql import Window

%pylab inline

Populating the interactive namespace from numpy and matplotlib
/databricks/python/lib/python3.8/site-packages/IPython/core/magics/pylab.py:159: UserWarning: pylab import has clobbered these variables: ['table', 'display']
`%matplotlib` prevents importing * from pylab and numpy
  warn("pylab import has clobbered these variables: %s"  % clobbered +


In [0]:
test_df = spark.read.format("csv")\
                     .option("header", "true")\
                     .option("inferschema", "true")\
                     .load("/FileStore/shared_uploads/test.csv")

train_df = spark.read.format("csv")\
                    .option("header", "true")\
                    .option("inferschema", "true")\
                    .load("/FileStore/shared_uploads/train.csv")

In [0]:
fill_na_func = lambda x: F.percentile_approx(x, 0.5)

def data_transformation(df, mode='train'):
  
  columns = df.columns
  notall_columns = df.columns
  notall_columns.remove('Id')
  notall_columns.remove('Week')
  if 'target' in notall_columns:
    notall_columns.remove('target')
    
  old_cols = [f'df{i}.{col}' for col in notall_columns for i in range(1,5) if not (i>1 and 'V' in col)]
  new_cols = [f'{col}_{i}' for col in notall_columns for i in range(1,5) if not (i>1 and 'V' in col)]

  w = Window.partitionBy(df.Id)
  for col in notall_columns:
    df = df.withColumn(col+"_agg", fill_na_func(F.col(col)).over(w))
    df = df.withColumn(col, F.when(F.col(col).isNull(), F.col(col+"_agg")).otherwise(F.col(col)))
  df = df.select(*columns)

    
  if mode == 'train':
    P_feat_df = df.select(*[col for col in df.columns if ("P" in col or "Id" in col or "Week" in col or "tar" in col)])
    joined_final_df = df.alias('df1')\
                                  .join(P_feat_df.alias('df2'), 
                                        on=((F.col('df1.Id') == F.col('df2.Id')) & (F.col('df1.Week') == F.col('df2.Week')-1)), 
                                        how='left')\
                                  .join(P_feat_df.alias('df3'), 
                                        on=((F.col('df1.Id') == F.col('df3.Id')) & (F.col('df1.Week') == F.col('df3.Week')-2)), 
                                        how='left')\
                                  .join(P_feat_df.alias('df4'), 
                                        on=((F.col('df1.Id') == F.col('df4.Id')) & (F.col('df1.Week') == F.col('df4.Week')-3)), 
                                        how='left')
    joined_final_df = joined_final_df.where(F.col('df1.Week') == 0)\
                                     .drop(F.col('df1.Week'))\
                                     .drop(F.col('df2.Week'))\
                                     .drop(F.col('df3.Week'))\
                                     .drop(F.col('df4.Week'))\
                                     .drop(F.col('df2.Id'))\
                                     .drop(F.col('df3.Id'))\
                                     .drop(F.col('df4.id'))\
                                     .drop(F.col('df1.target'))\
                                     .drop(F.col('df2.target'))\
                                     .drop(F.col('df3.target'))
    
    joined_final_df = joined_final_df.select('Id', *list(map(lambda x, y: F.col(x).alias(y), old_cols, new_cols)), 'target')
    return joined_final_df
    
  if mode == 'test':
    P_feat_df = df.select(*[col for col in df.columns if ("P" in col or "Id" in col or "Week" in col)])
    joined_final_df = df.alias('df1')\
                                  .join(P_feat_df.alias('df2'), 
                                        on=((F.col('df1.Id') == F.col('df2.Id')) & (F.col('df1.Week') == F.col('df2.Week')-1)), 
                                        how='left')\
                                  .join(P_feat_df.alias('df3'), 
                                        on=((F.col('df1.Id') == F.col('df3.Id')) & (F.col('df1.Week') == F.col('df3.Week')-2)), 
                                        how='left')\
                                  .join(P_feat_df.alias('df4'), 
                                        on=((F.col('df1.Id') == F.col('df4.Id')) & (F.col('df1.Week') == F.col('df4.Week')-3)), 
                                        how='left')
    joined_final_df = joined_final_df.where(F.col('df1.Week') == 0)\
                                     .drop(F.col('df1.Week'))\
                                     .drop(F.col('df2.Week'))\
                                     .drop(F.col('df3.Week'))\
                                     .drop(F.col('df4.Week'))\
                                     .drop(F.col('df2.Id'))\
                                     .drop(F.col('df3.Id'))\
                                     .drop(F.col('df4.id'))       
    
    joined_final_df = joined_final_df.select('Id', *list(map(lambda x, y: F.col(x).alias(y), old_cols, new_cols)))
    return joined_final_df                  

In [0]:
#another solution fod data aggregation

# joined = train_df.alias('df1')\
#                 .join(train_df.alias('df2'), on=((F.col('df1.Id') == F.col('df2.Id')) & (F.col('df1.Week') == F.col('df2.Week')-1)), how='left')\
#                 .join(train_df.alias('df3'), on=((F.col('df1.Id') == F.col('df3.Id')) & (F.col('df1.Week') == F.col('df3.Week')-2)), how='left')\
#                 .join(train_df.alias('df4'), on=((F.col('df1.Id') == F.col('df4.Id')) & (F.col('df1.Week') == F.col('df4.Week')-3)), how='left')
                                                 
# joined = joined.where(F.col('df1.Week') == 0 )\
#                .drop(F.col('df2.Week'))\
#                .drop(F.col('df3.Week'))\
#                .drop(F.col('df4.Week'))\
#                .drop(F.col('df2.Id'))\
#                .drop(F.col('df3.Id'))\
#                .drop(F.col('df4.id'))\
#                .drop(F.col('df2.target'))\
#                .drop(F.col('df3.target'))\
#                .drop(F.col('df4.target'))

# columns = train_df.columns
# columns.remove('Id')
# columns.remove('Week')
# columns.remove('target')

# coefs = (2, 1, 1, 1)
# for col in columns:
#   joined = joined.withColumn(col+'_new', (coefs[0]*F.col(f'df1.{col}') + 
#                                          coefs[1]*F.col(f'df2.{col}') + 
#                                          coefs[2]*F.col(f'df3.{col}') + 
#                                          coefs[3]*F.col(f'df4.{col}'))/4)
# final_df = joined.select(F.col('df1.Id').alias('Id'), *[F.col(col+'_new').alias(col) for col in columns], F.col('df1.target').alias('target'))
# # final_df.display()

In [0]:
train_final = data_transformation(train_df, mode='train')
test_final = data_transformation(test_df, mode='test')
train_final.display()

Id V1_1 V2_1 V3_1 V4_1 V5_1 V6_1 V7_1 V8_1 V9_1 V10_1 V11_1 V12_1 V13_1 V14_1 V15_1 V16_1 V17_1 V18_1 V19_1 V20_1 V21_1 V22_1 P1_1 P1_2 P1_3 P1_4 P2_1 P2_2 P2_3 P2_4 P3_1 P3_2 P3_3 P3_4 P4_1 P4_2 P4_3 P4_4 P5_1 P5_2 P5_3 P5_4 P6_1 P6_2 P6_3 P6_4 P7_1 P7_2 P7_3 P7_4 P8_1 P8_2 P8_3 P8_4 P9_1 P9_2 P9_3 P9_4 P10_1 P10_2 P10_3 P10_4 P11_1 P11_2 P11_3 P11_4 P12_1 P12_2 P12_3 P12_4 P13_1 P13_2 P13_3 P13_4 P14_1 P14_2 P14_3 P14_4 P15_1 P15_2 P15_3 P15_4 P16_1 P16_2 P16_3 P16_4 P17_1 P17_2 P17_3 P17_4 P18_1 P18_2 P18_3 P18_4 P19_1 P19_2 P19_3 P19_4 P20_1 P20_2 P20_3 P20_4 P21_1 P21_2 P21_3 P21_4 P22_1 P22_2 P22_3 P22_4 P23_1 P23_2 P23_3 P23_4 P24_1 P24_2 P24_3 P24_4 P25_1 P25_2 P25_3 P25_4 P26_1 P26_2 P26_3 P26_4 P27_1 P27_2 P27_3 P27_4 target -9173346003017351704 0.5384615384615384 9.0 null null null null null null null null null null null null null null null null null null null null 58.0 63.0 52.0 58.0 24502.0 23840.0 33436.0 24502.0 0.04 0.11428571428571428 0.25925925925925924 0.11428571428571428 3.72967854922911 4.576432884525668 3.2050451327764944 3.72967854922911 33.88333333333333 33.583333333333336 47.68333333333333 33.88333333333333 10.5 8.483333333333333 12.9 10.5 136.02 132.88571428571427 162.37037037037038 136.02 0.14 0.17142857142857143 0.0 0.14 0.08 0.17142857142857143 0.0 0.08 0.14 0.2 0.18518518518518517 0.18518518518518517 0.26 0.2857142857142857 0.37037037037037035 0.2857142857142857 4.89 4.93 4.93 4.93 0.1 0.05714285714285714 0.037037037037037035 0.05714285714285714 1983.4807692307693 2195.027027027027 2225.96875 2195.027027027027 81.25 65.56666666666666 98.05 81.25 0.2 0.2571428571428571 0.1111111111111111 0.2 9.224318658280922 9.040697674418604 6.883720930232558 9.040697674418604 11610.16 11354.542857142857 14477.962962962964 11610.16 27.6 16.883333333333333 45.85 27.6 4.93 4.93 4.93 4.93 9.931333333333335 8.77142857142857 13.495061728395061 9.931333333333335 221.0 245.0 301.0 245.0 0.0 0.0 0.0 0.0 4.906799999999995 4.930000000000004 4.930000000000003 4.930000000000003 0.74 0.5428571428571428 0.7407407407407407 0.74 2117.0 659.0 3053.0 2117.0 0.3 0.2 0.2962962962962963 0.2962962962962963 0.0 -9152034383903842080 0.02564102564102564 1.0 0.0 0.1492774024024024 0.006756756756756757 0.0 0.270289039039039 0.12390202702702703 0.013513513513513514 0.027777777777777776 0.015625 0.19852665165165165 0.0 0.0 0.0 0.0 0.006756756756756757 0.0 0.0 0.17406156156156155 0.013513513513513514 0.0 85.0 137.0 70.0 68.0 14823.0 14648.0 19466.0 43364.0 0.7333333333333333 0.8888888888888888 0.75 0.8378378378378378 2.674659989691291 2.6460335908874266 2.864932899676759 2.839501872730328 30.85 41.7 43.55 63.1 16.65 26.35 14.883333333333333 15.333333333333334 118.73333333333333 165.88888888888889 150.625 159.0810810810811 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.02702702702702703 0.26666666666666666 0.0 0.0625 0.08108108108108109 0.26666666666666666 0.5555555555555556 0.3125 0.2972972972972973 4.92 4.92 4.92 4.91 0.0 0.0 0.0625 0.05405405405405406 1483.3529411764705 1500.9 1499.4736842105262 1527.8536585365853 56.5 82.93333333333334 87.56666666666666 499.73333333333335 0.4 0.0 0.125 0.24324324324324326 4.492254733218589 4.163855421686747 6.143171806167401 7.462686567164179 8568.266666666666 12219.444444444445 11236.75 11961.54054054054 17.966666666666665 12.033333333333333 23.966666666666665 37.05 4.92 4.92 4.92 4.92 9.35888888888889 8.231481481481481 9.494791666666668 10.445495495495498 170.0 234.0 228.0 500.0 0.0 0.0 0.0 0.02702702702702703 4.920000000000001 4.920000000000001 4.920000000000001 4.916486486486483 0.26666666666666666 0.1111111111111111 0.25 0.10810810810810811 3572.0 8553.0 1728.0 3507.0 0.06666666666666667 0.4444444444444444 0.4375 0.32432432432432434 0.0 -9147768078838301331 0.48717948717948717 14.0 0.004166666666666667 0.013383665065202471 0.056864847860901395 0.050725663463738274 0.00948581560283688 0.01729831560283688 0.1449189258750858 0.0 0.3480292696179364 0.0 0.008333333333333333 0.07424359414321666 0.10260380919698009 0.1359811

In [0]:
test_final.display()

Id V1_1 V2_1 V3_1 V4_1 V5_1 V6_1 V7_1 V8_1 V9_1 V10_1 V11_1 V12_1 V13_1 V14_1 V15_1 V16_1 V17_1 V18_1 V19_1 V20_1 V21_1 V22_1 P1_1 P1_2 P1_3 P1_4 P2_1 P2_2 P2_3 P2_4 P3_1 P3_2 P3_3 P3_4 P4_1 P4_2 P4_3 P4_4 P5_1 P5_2 P5_3 P5_4 P6_1 P6_2 P6_3 P6_4 P7_1 P7_2 P7_3 P7_4 P8_1 P8_2 P8_3 P8_4 P9_1 P9_2 P9_3 P9_4 P10_1 P10_2 P10_3 P10_4 P11_1 P11_2 P11_3 P11_4 P12_1 P12_2 P12_3 P12_4 P13_1 P13_2 P13_3 P13_4 P14_1 P14_2 P14_3 P14_4 P15_1 P15_2 P15_3 P15_4 P16_1 P16_2 P16_3 P16_4 P17_1 P17_2 P17_3 P17_4 P18_1 P18_2 P18_3 P18_4 P19_1 P19_2 P19_3 P19_4 P20_1 P20_2 P20_3 P20_4 P21_1 P21_2 P21_3 P21_4 P22_1 P22_2 P22_3 P22_4 P23_1 P23_2 P23_3 P23_4 P24_1 P24_2 P24_3 P24_4 P25_1 P25_2 P25_3 P25_4 P26_1 P26_2 P26_3 P26_4 P27_1 P27_2 P27_3 P27_4 -9193687728771344321 0.10256410256410256 3.0 0.004260651629072682 0.040318186771276014 0.016337038247793395 0.0 0.5409965130216847 0.15137844611528822 0.006641604010025063 0.011904761904761904 0.02566742944317315 0.013266862809196905 0.0 0.010937670262613055 0.10835785114961316 0.004192546583850932 0.0 0.0 0.0 0.06574043805165086 0.0 0.0 79.0 70.0 65.0 53.0 46682.0 45016.0 17453.0 38504.0 0.3142857142857143 0.43884892086330934 0.6666666666666666 0.41044776119402987 3.987763734189376 4.50141620710189 3.9697954489335503 3.6979019594420004 28.566666666666666 25.05 23.816666666666666 25.85 7.5 8.283333333333333 8.866666666666667 7.233333333333333 169.56190476190477 153.59420289855072 149.9047619047619 159.29323308270676 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.1523809523809524 0.16666666666666666 0.14285714285714285 0.19548872180451127 0.2 0.26811594202898553 0.19047619047619047 0.2556390977443609 5.0 5.0 5.0 5.0 0.009523809523809525 0.007246376811594203 0.047619047619047616 0.007518796992481203 1945.8157894736842 1994.3125 2014.98 1775.8280254777071 84.61666666666666 58.75 47.78333333333333 59.483333333333334 0.2 0.21014492753623187 0.21428571428571427 0.18796992481203006 11.982507288629737 16.269430051813472 8.492682926829268 12.25296442687747 11063.466666666667 9053.81884057971 7873.952380952381 8397.721804511279 19.35 23.35 22.3 48.483333333333334 5.0 5.0 5.0 5.0 8.560317460317462 8.337170263788964 8.453571428571426 9.04291044776119 504.0 451.0 261.0 507.0 0.02857142857142857 0.02158273381294964 0.0 0.014925373134328358 5.0 5.0 5.0 5.0 0.6571428571428571 0.539568345323741 0.3333333333333333 0.5746268656716418 1285.0 2329.0 1173.0 1414.0 0.4380952380952381 0.34782608695652173 0.40476190476190477 0.3533834586466165 -9190465597412250947 0.05128205128205128 1.0 0.0 0.016051472168493446 0.0 0.004310344827586207 0.07666540681947873 0.02999131075983607 0.003787878787878788 0.0 0.24516904184915925 0.0 0.0 0.18321976181477284 0.3166741701683008 0.0 0.0 0.0 0.0 0.1005612804493949 0.023569332355099046 0.0 47.0 52.0 53.0 47.0 24735.0 16326.0 18677.0 12598.0 0.1896551724137931 0.14893617021276595 0.15151515151515152 0.22857142857142856 2.717834415392814 2.9803228936883217 3.0265137880769353 2.4376030691412507 22.75 24.433333333333334 20.55 24.583333333333332 8.4 9.25 7.75 8.833333333333334 101.55172413793103 100.76595744680851 88.4090909090909 98.19444444444444 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.08620689655172414 0.10638297872340426 0.07575757575757576 0.1111111111111111 0.08620689655172414 0.06382978723404255 0.12121212121212122 0.16666666666666666 4.96 4.96 4.96 4.96 0.39655172413793105 0.425531914893617 0.5757575757575758 0.4166666666666667 1070.3529411764705 1092.0566037735848 1102.887323943662 1095.4634146341464 62.8 63.71666666666667 51.1 51.3 0.3793103448275862 0.3191489361702128 0.19696969696969696 0.2777777777777778 7.256637168141593 11.07843137254902 8.072916666666666 6.658291457286432 6895.517241379311 6452.04255319149 5928.80303030303 5984.111111111111 28.6 14.166666666666666 16.65 16.7 4.96 4.96 4.96 4.96 7.626149425287356 6.9822695035460995 6.524494949494951 7.720476190476191 438.0 260.0 205.0 162.0 0.0 0.0 0.0 0.0 4.96 4.960000000000002 4.959999999999997 4.96 0.8103448275862069 0.851063829787234 0.84848484848

In [0]:
train_final.coalesce(1).write.format("csv")\
                             .option("header", True)\
                             .mode("overwrite")\
                             .save('/FileStore/tables/results_tr/') 

test_final.coalesce(1).write.format("csv")\
                            .option("header", True)\
                            .mode("overwrite")\
                            .save('/FileStore/tables/results_ts/') 